# Cell 1: Setup Dependencies

In [1]:
import cv2
import numpy as np
from ultralytics import YOLO
from deep_sort_realtime.deepsort_tracker import DeepSort
import time
import sqlite3
import logging

logging.basicConfig(filename='debug.log', level=logging.DEBUG)

# Cell 2: Load Models

In [2]:
# Load YOLOv8 model
model = YOLO("yolov8s.pt")

# Initialize DeepSORT tracker
tracker = DeepSort(max_age=30, nn_budget=100)


# Cell 3: Define Video Sources

In [3]:
# Define video sources
video_sources = ["video1.mp4", "video2.mp4"]  # Replace with actual camera feeds
caps = [cv2.VideoCapture(src) for src in video_sources]


# Cell 4: Global Tracking Variables

In [4]:
# Global tracking dictionary {global_id: {"features": (color_hist, body_size), "last_seen": timestamp, "camera": cam_id}}
global_tracks = {}

# Store last detected positions to prevent ghost boxes
last_positions = {}  # {global_id: (x1, y1, x2, y2)}

# Store rectangles for click detection
rectangles = {}


# Cell 5: Mouse Click Callback

In [5]:
# Mouse callback function to handle rectangle click
def click_callback(event, x, y, flags, param):
    if event == cv2.EVENT_LBUTTONDOWN:
        logging.debug(f"Mouse clicked at ({x}, {y})")
        for global_id, rect in rectangles.items():
            x1, y1, x2, y2, color = rect
            if x1 <= x <= x2 and y1 <= y <= y2:
                # Toggle color between red and green on click
                new_color = (0, 255, 0) if color == (0, 0, 255) else (0, 0, 255)
                rectangles[global_id] = (x1, y1, x2, y2, new_color)
                logging.debug(f"Rectangle with ID {global_id} clicked and color changed")


# Cell 6: Database Functions

In [6]:
# Connect to SQLite database
def connect_db():
    return sqlite3.connect('person_tracking.db')

# Store person information in the database
def store_person_info(global_id, features, body_size, last_seen, location):
    conn = sqlite3.connect('person_data.db')
    cursor = conn.cursor()

    cursor.execute('''CREATE TABLE IF NOT EXISTS persons (
                        global_id INTEGER PRIMARY KEY, 
                        color_hist BLOB, 
                        body_size REAL, 
                        last_seen REAL, 
                        x1 REAL, y1 REAL, x2 REAL, y2 REAL)''')

    cursor.execute('''INSERT OR REPLACE INTO persons 
                      (global_id, color_hist, body_size, last_seen, x1, y1, x2, y2) 
                      VALUES (?, ?, ?, ?, ?, ?, ?, ?)''', 
                   (global_id, features, body_size, last_seen, *location))

    conn.commit()
    conn.close()


# Cell 7: Feature Extraction

In [7]:
# Function to extract dominant clothing color
def extract_color_histogram(image, bbox):
    x1, y1, x2, y2 = map(int, bbox)
    person_crop = image[y1:y2, x1:x2]
    hsv = cv2.cvtColor(person_crop, cv2.COLOR_BGR2HSV)
    hist = cv2.calcHist([hsv], [0, 1], None, [8, 8], [0, 180, 0, 256])
    cv2.normalize(hist, hist)
    return hist.flatten()


# Cell 8: Person Matching

In [8]:
# Function to match persons across feeds
def find_matching_person(new_hist, new_size, cam_id, threshold=100):
    best_match = None
    best_score = float("inf")

    for track_id, data in global_tracks.items():
        if data["camera"] == cam_id:
            continue  # Skip if the person is already tracked in this camera

        old_hist, old_size = data["features"]
        size_diff = abs(new_size - old_size) / old_size
        color_score = cv2.compareHist(new_hist, old_hist, cv2.HISTCMP_CORREL)

        if size_diff < 200 and color_score > threshold:
            if color_score < best_score:
                best_score = color_score
                best_match = track_id

    return best_match


# Cell 9: Video Processing Function

In [9]:
# Process each video stream
def process_video(cap, cam_id):
    if not cap.isOpened():
        print(f"Error: Couldn't open video {video_sources[cam_id]}")
        return

    fps = int(cap.get(cv2.CAP_PROP_FPS))
    width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

    if width == 0 or height == 0:
        print("Error: Couldn't retrieve video dimensions.")
        return

    out = cv2.VideoWriter(f"output_camera_{cam_id}.mp4", cv2.VideoWriter_fourcc(*'mp4v'), fps, (width, height))

    window_name = f"Camera {cam_id}"
    cv2.namedWindow(window_name)
    cv2.setMouseCallback(window_name, click_callback)

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break  

        results = model(frame)
        detections = []
        track_map = {}

        for r in results:
            for box in r.boxes:
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                conf = float(box.conf[0])
                cls = int(box.cls[0])

                if cls == 0 and conf > 0.6:
                    bbox = [x1, y1, x2-x1, y2-y1]
                    color_hist = extract_color_histogram(frame, (x1, y1, x2, y2))
                    body_size = (y2 - y1) * (x2 - x1)

                    matched_id = find_matching_person(color_hist, body_size, cam_id)

                    global_id = matched_id if matched_id else len(detections) + 1
                    global_tracks[global_id] = {"features": (color_hist, body_size), "last_seen": time.time(), "camera": cam_id}

                    track_map[len(detections)] = global_id
                    detections.append((bbox, conf, "person"))
                    store_person_info(global_id, color_hist, body_size, time.time(), (x1, y1, x2, y2))

        tracks = tracker.update_tracks(detections, frame=frame)

        for i, track in enumerate(tracks):
            if track.is_confirmed():
                bbox = track.to_tlbr()
                global_id = track_map.get(track.track_id, track.track_id)
                last_positions[global_id] = bbox  

                color = rectangles.get(global_id, (0, 0, 0, 0, (0, 255, 0)))[4]
                cv2.rectangle(frame, (int(bbox[0]), int(bbox[1])), (int(bbox[2]), int(bbox[3])), color, 2)
                cv2.putText(frame, f"ID {global_id} (Cam {cam_id})", (int(bbox[0]), int(bbox[1]) - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, color, 2)

                rectangles[global_id] = (int(bbox[0]), int(bbox[1]), int(bbox[2]), int(bbox[3]), color)

        cv2.imshow(window_name, frame)
        out.write(frame)

        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    out.release()
    cv2.destroyWindow(window_name)


# Cell 10: Run Video Processing

In [10]:
# Run the video processing for each camera sequentially
for i, cap in enumerate(caps):
    process_video(cap, i)

cv2.destroyAllWindows()


0: 384x640 4 persons, 1 handbag, 96.9ms
Speed: 6.9ms preprocess, 96.9ms inference, 241.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 3 handbags, 74.6ms
Speed: 6.8ms preprocess, 74.6ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 3 handbags, 35.4ms
Speed: 2.9ms preprocess, 35.4ms inference, 2.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 4 persons, 3 handbags, 35.4ms
Speed: 3.0ms preprocess, 35.4ms inference, 2.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 3 handbags, 33.5ms
Speed: 2.9ms preprocess, 33.5ms inference, 3.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 3 handbags, 34.1ms
Speed: 3.0ms preprocess, 34.1ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 3 handbags, 33.3ms
Speed: 2.8ms preprocess, 33.3ms inference, 4.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 5 persons, 3 h

# DATABASE

In [11]:
import sqlite3

def display_all_person_data():
    # Connect to the database
    conn = sqlite3.connect('person_data.db')  # Replace with your actual database file path
    cursor = conn.cursor()
    
    # Query to select all records from the 'persons' table
    cursor.execute("SELECT * FROM persons")
    
    # Fetch all rows
    rows = cursor.fetchall()

    # Display all records
    for row in rows:
        print(f"Global ID: {row[0]}")
        print(f"Color Histogram: {row[1]}")
        print(f"Body Size: {row[2]}")
        print(f"Last Seen: {row[3]}")
        print(f"Location (x1, y1, x2, y2): ({row[4]}, {row[5]}, {row[6]}, {row[7]})")
        print("-" * 50)
    
    # Close the connection
    conn.close()

# Call the function to display all records
display_all_person_data()

Global ID: 1
Color Histogram: b'\x19H??\xc0\x87\xb0>{\x0c\xdc=n7\xd6=M\r\xbb<\x80\x19\xdd;\xa9\x8d\x8b;%\x9f_<A\xd7\xf1>\xa02\xc2<\xc0K\'<\xfc\xeea=\xa9\x8d\x8b;\x1fP<9\x00\x00\x00\x00\xff6\xd78a\x83\xe1<\xdf\x1d\xf29\x00\x00\x00\x00\xff6\xd77\xff6W8\xff6W8\x00\x00\x00\x00\xff6\xd78\xeb\x7f\xe9=\x19\x01\x19;\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00\x9cgc=.6\xf8<\xf7"(;\xfb\xac\xbf;\xe0d\x0c=\xb5+\xd2=.\xb9a=\x1f\xb2\x94=\xe1DV=\x9em\xb6<\xf6\x1c\xd5<r\xb6\x8a<O\x91\x7f<\x8c\xbc\x9b<\x9c\xa8\xaa<9\x0f\'>a&\x01=\x12k\xdb;\x91\xc9\x1c<N\x13\x0e<\'d\xeb:\xf7"\xa8:\x97\xd7x:#\x1b\x1b<C\xd2\'=#\xda\xd3;\xb9\xb5i;\xd1\xba\x1f;\xf3\x98\x10;G}\xd0:C\xf3\xb8:%\x9f_;'
Body Size: 112608.0
Last Seen: 1739814026.88488
Location (x1, y1, x2, y2): (584.0, 163.0, 788.0, 715.0)
--------------------------------------------------
Global ID: 2
Color Histogram: b'x2\x15??\xe9\x18?\xefn\x05>Y\x95\x1e>\x02\xecL=W\x99E=%\x80\x97<\x13y\xb6<n\xcb\xec=\xf8\x0b